In [1]:
import plotly
import plotly.graph_objs as go
from IPython.display import display, HTML
plotly.offline.init_notebook_mode(connected=True)

In [2]:
from rainman2 import RAINMAN2

Rainman2's logging has been configured!


Using TensorFlow backend.



#### Normal case: Start with 30% Random actions (explore) and rest 70% fetch max actions (exploit)


In [3]:
# Server profile: num_ues=200, APs=16, Scale=200.0, explore_radius=1
from collections import OrderedDict
ALGORITHM_CONFIG = OrderedDict(
    EPISODES=400,
    ALPHA=0.2,
    GAMMA=0.9,
    EPSILON=0.3,
    EPSILON_DECAY=0.99,
    EPSILON_MIN=0.01,
    VERBOSE=True,
    L1_HIDDEN_UNITS=13,
    L2_HIDDEN_UNITS=13,
    L1_ACTIVATION='relu',
    L2_ACTIVATION='relu',
    LOSS_FUNCTION='mean_squared_error',
    OPTIMIZER='Adam',
)

CELLULAR_MODEL_CONFIG = OrderedDict(
    NAME='Cellular',
    TYPE='Dev',
    SERVER='0.0.0.0',
    SERVER_PORT='8000',
    VERBOSE=True,
)


In [4]:
RAINMAN2.algorithm_config = ALGORITHM_CONFIG
RAINMAN2.environment_config = CELLULAR_MODEL_CONFIG

In [5]:
result = RAINMAN2.run_experiment("Cellular", "Qlearning", "Naive")

2018-04-26 09:34:51,333 Aris-MacBook-Pro.local Rainman2[4429] INFO Starting experiment!
2018-04-26 09:34:51,335 Aris-MacBook-Pro.local Rainman2[4429] INFO Building Environment instance: Cellular
2018-04-26 09:34:51,337 Aris-MacBook-Pro.local rainman2.lib.environment.cellular.base[4429] INFO Instantiating Cellular client: Dev
2018-04-26 09:34:51,339 Aris-MacBook-Pro.local QCellularAgent[4429] INFO Configuration used for the QCellular Agent:
2018-04-26 09:34:51,340 Aris-MacBook-Pro.local QCellularAgent[4429] INFO episodes: 400
2018-04-26 09:34:51,341 Aris-MacBook-Pro.local QCellularAgent[4429] INFO alpha: 0.2
2018-04-26 09:34:51,341 Aris-MacBook-Pro.local QCellularAgent[4429] INFO gamma: 0.9
2018-04-26 09:34:51,342 Aris-MacBook-Pro.local QCellularAgent[4429] INFO epsilon: 0.3
2018-04-26 09:34:51,343 Aris-MacBook-Pro.local QCellularAgent[4429] INFO epsilon_decay: 0.99
2018-04-26 09:34:51,344 Aris-MacBook-Pro.local QCellularAgent[4429] INFO epsilon_min: 0.01
2018-04-26 09:34:51,345 Aris-Ma

Module: run_experiment took: 207.49503299999998s


[========================================================================] 100%


In [6]:
print("Number of states encountered: {}".format(len(result.Q)))

Number of states encountered: 3791


In [7]:
print("Number of q_ap_states encountered: {}".format(len(result.Q_ap)))

Number of q_ap_states encountered: 1269


In [ ]:
print(result.Q)

In [ ]:
print(result.Q_ap)

In [ ]:
print(result.UE_AP_LIST)

In [8]:
ue_ap_list = [x.location for x in result.UE_AP_LIST]

ap_custom_colors = 'rgb(230, 25, 75)'
ue_custom_colors = 'rgb(0, 130, 200)'

ap_x, ap_y = list(zip(*ue_ap_list[:16]))
ue_x, ue_y = list(zip(*ue_ap_list[16:]))

aps = go.Scatter(
    x = ap_x,
    y = ap_y,
    mode = 'markers',
    marker = {'color': ap_custom_colors, 'size': 15},
    name = 'APs'
)

ues = go.Scatter(
    x = ue_x,
    y = ue_y,
    mode = 'markers',
    marker = {'color': ue_custom_colors},
    name = 'UEs'
)


data = [aps, ues]


# Plot and embed in ipython notebook!
layout = dict(xaxis={'range': [0, 1500], 'title': 'x'},
              yaxis={'range': [0, 1500], 'title': 'y'},
              title="UE and AP Distribution in the grid",
              height=500,
              width=800,
              showlegend=True
              )

fig = dict(data=data, layout=layout)

plotly.offline.iplot(fig)

In [9]:
# Create rewards graph
rewards = go.Scatter(
    x = len(result.Rewards),
    y = result.Rewards,
    name='Rewards'
)

data = [rewards]


# Plot and embed in ipython notebook!
plotly.offline.iplot(
    {"data": data,
     "layout": go.Layout(
         height=500,
         width=800,
         title="Rewards over time",
         xaxis=dict(
             title='Episodes',
         ),
         yaxis=dict(
             title='Rewards',
         ), 
         showlegend=True)},
    show_link=False,
    link_text=None)



In [10]:
# Create handoff graph
handoffs = go.Scatter(
    x = len(result.Handoffs),
    y = result.Handoffs,
    name='Handoffs'
)

data = [handoffs]

# Plot and embed in ipython notebook!
plotly.offline.iplot(
    {"data": data,
     "layout": go.Layout(
         height=500,
         width=800,
         title='Handoffs over time',
         xaxis=dict(
             title='Episodes',
         ),
         yaxis=dict(
             title='Handoffs'
         ), 
         showlegend=True)},
    show_link=False,
    link_text=None)


In [11]:
# Create UE graph
ue_sla = go.Scatter(
    x = len(result.Meets_SLA),
    y = result.Meets_SLA,
    name='UE SLA'
)

data = [ue_sla]

# Plot and embed in ipython notebook!
plotly.offline.iplot(
    {"data": data,
     "layout": go.Layout(
         height=500,
         width=800,
         title="UE's SLA over time",
         xaxis=dict(
             title='Episodes',
         ),
         yaxis=dict(
             title='UE SLA'
         ), 
         showlegend=True)},
    show_link=False,
    link_text=None)